In [32]:
from pymongo import MongoClient
from pathlib import Path
import os
from pprint import pprint
import nltk
import matplotlib.pyplot as plt
import pprint

import os
import struct
import matplotlib
from scipy import signal
import numpy as np
import sys
import pymongo
%matplotlib inline

In [20]:
client = MongoClient('mongodb://localhost:27017')
testDb = client.testDb

In [21]:
patients = testDb.patients
sessions = testDb.sessions
reports = testDb.reports

In [22]:
def fileName(filePath):
    return (os.path.splitext(os.path.split(filePath)[1]))[0]

def fileExt(filePath):
    try:
        return (os.path.splitext(os.path.split(filePath)[1]))[1]
    except:
        return "Error"

In [23]:
p1 = os.listdir("v1.2.0/eval")
print(p1)
print(os.path.isdir(p1[0]))
print(os.path.isfile(p1[1]))
pathString = ("/"+str(p1[0]))
print(pathString)
patientDict = {}
fileNames = []
maxFileSize = 0 
maxFileName = ""
for root,dirs,files in os.walk("v1.2.0"):
    #print ("root: ",root)
    #print("\tdirs: ",dirs)
    #print("\t\t",str(files))
        
    if len(files)>0:
        for file in files:
            fileNames.append(str(root)+"/"+str(file))
            if os.path.getsize((str(root)+"/"+file)) > maxFileSize:
                maxFileSize = os.path.getsize((str(root)+"/"+file))
                maxFileName = (str(root)+"/"+file)
            else:
                continue
            
            
        #print ("\t\tFile: "+files[3])
        
print (maxFileName," : ",maxFileSize)
print (os.path.splitext(maxFileName))
print (os.path.split(maxFileName))
print (os.path.splitext(os.path.split(maxFileName)[1]))
print (fileName(maxFileName))
print (fileExt(maxFileName))

['03_tcp_ar_a', '02_tcp_le', '.DS_Store', '01_tcp_ar']
False
False
/03_tcp_ar_a
v1.2.0/eval/01_tcp_ar/00001278/s002_2003_11_17/00001278_s002_t001.edf  :  67899648
('v1.2.0/eval/01_tcp_ar/00001278/s002_2003_11_17/00001278_s002_t001', '.edf')
('v1.2.0/eval/01_tcp_ar/00001278/s002_2003_11_17', '00001278_s002_t001.edf')
('00001278_s002_t001', '.edf')
00001278_s002_t001
.edf


In [86]:
def addFile(filepath):
    splitFile = filepath.split('/')
    if len(splitFile)<6:
        pass
        #print("File path too short")
    else:
        patientId = splitFile[3]
        currentFile = splitFile[5] #changed from 5 to 4
        currentSessionNumber = splitFile[4].split('_')[0]
        currentFileSplit = currentFile.split('_')
        currentFileExt = str(fileExt(currentFile))
        sessionNumber = currentFileSplit[0] #Changed from 1 to 0
        sessionId = str(patientId)+str(currentSessionNumber)
        #print("\tFile Path: ",filepath)
        #print("\t\tCurrentFile: ",currentFileSplit)
        #print("\t\tCurrentFileExt: ",currentFileExt)
        #print("\t\tSessionId: ",sessionId)
        dbSession = sessions.find_one({"sessionId":sessionId})
        
        if dbSession == None:
            sessions.insert_one({"sessionId":sessionId,"patientId":patientId})
            #print("Found a new session")
        else:
            pass
            #print("Found this session\n")  
        if currentFileExt == ".txt":
            try:
                with open(str(files),'r') as reportFile:
                    rText = reportFile.readlines()  
                try:
                    sessions.update_one({"sessionId":sessionId},
                                       {"$set":{"reportText":rText}})
                except:
                    pass
                    #print("Could not add report text")     
            except UnicodeDecodeError:
                sessions.update_one({"sessionId":sessionId},
                                       {"$set":{"reportText":"Unopenable"}})
        elif currentFileExt  == ".edf":
            try:
                updateEdf = dbSession['edfList']
                updateEdf.append(filepath)
                sessions.update_one({"sessionId":sessionId},{"$set":{"edfList":updateEdf}})    
            except:
                #print ("No edf") 
                sessions.update_one({"sessionId":sessionId},{"$set":{"edfList":[filepath]}})
        elif currentFileExt == ".lbl":
            try:
                updateLbl = dbSession['lblList']
                updateLbl.append(filepath)
                #print("\n\nUPDATING LABL LIST-------------")
                #print(updateLbl)
                sessions.update_one({"sessionId":sessionId},{"$set":{"lblList":updateLbl}})
            except:
                sessions.update_one({"sessionId":sessionId},{"$set":{"lblList":[filepath]}})
                
    #TSE DATA ERROR IN FIRST ENTRY BECAUSE dbSessionTSEDATA DOESNT EXIST
        elif currentFileExt == ".tse":
            try:
                updateTse = dbSession['tseList']
                updateTse.append(filepath)
                updateTseData = dbSession['tseData']
                tseEntry = parseTse(files)
                for entry in tseEntry:    
                    updateTseData.append(tseEntry)
                print(updateTseData)
                sessions.update_one({"sessionId":sessionId},{"$set":{"tseList":updateTse}})
                sessions.update_one({"sessionId":sessionId},{"$set":{"tseData":updateTseData}})
            
            except Exception as exc:
                print("TSE EXCEPTION ENCOUNTERED")
                print("EXC: ",exc)
                sessions.update_one({"sessionId":sessionId},{"$set":{"tseList":[filepath]}})
                
                tseEntry = parseTse(files)
    
                sessions.update_one({"sessionId":sessionId},{"$set":{"tseData":[tseEntry]}})
            

In [87]:
def parseTse(filePath):
    try:
        with open(str(filePath),'r') as tseFileData:
            tseData = [line.rstrip('\n') for line in tseFileData]
        print("Entry (Parse Fuction: ): ",tseData)
        tseEntryList = []
        for entry in tseData:
            entryList = entry.split(" ")
            print("TSE DATA ENTRY (parse function) : ",entryList)
            if len(entryList) == 4:
                splitFile = filePath.split('/')
                currentFile = splitFile[5] #changed from 5 to 4
                currentSessionNumber = splitFile[4].split('_')[0]
                currentFileSplit = currentFile.split('_')
                currentT = currentFileSplit[2].split(".")
                currentT = currentT[0]
                tseEntry = {'currentT':currentT,'startTime':entryList[0],'endTime':entryList[1],
                               'eventLabel':entryList[2],'probability':entryList[3]}
                tseEntryList.append(tseEntry)
            else:
                print("LEN NOT 4: ",entryList)
        return(tseEntryList)
    except Exception as exc:
        print("Exception: ",exc)
        print("Found an error with tseFile()")

In [88]:
testTextFileRecords  = testDb.sessions.find({}).limit(1)
for x in testTextFileRecords:
    #print(x['edfList'],'\n')
    #print(x['tseList'])
    tseFile = x['tseList'][0]
    print("TSE FROM PARSE FUNCTION: ",x['tseData'],'\n')

print(tseFile)
with open(str(tseFile),'r') as tseFileData:
            tseData = [line.rstrip('\n') for line in tseFileData]
#print("TSE DATA FROM FILE: ",tseData)
for x in tseData:
    print("\t",x,'\n')
parseTse(tseFile)

TSE FROM PARSE FUNCTION:  [[{'currentT': 't002', 'startTime': '0.0000', 'endTime': '62.9323', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't002', 'startTime': '62.9323', 'endTime': '153.2431', 'eventLabel': 'fnsz', 'probability': '1.0000'}, {'currentT': 't002', 'startTime': '153.2431', 'endTime': '405.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't003', 'startTime': '0.0000', 'endTime': '434.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't001', 'startTime': '0.0000', 'endTime': '425.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't000', 'startTime': '0.0000', 'endTime': '345.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}]] 

v1.2.0/eval/03_tcp_ar_a/00005943/s002_2009_06_28/00005943_s002_t002.tse
	 version = tse_v1.0.0 

	  

	 0.0000 62.9323 bckg 1.0000 

	 62.9323 153.2431 fnsz 1.0000 

	 153.2431 405.0000 bckg 1.0000 

Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 62.9323 

[{'currentT': 't002',
  'endTime': '62.9323',
  'eventLabel': 'bckg',
  'probability': '1.0000',
  'startTime': '0.0000'},
 {'currentT': 't002',
  'endTime': '153.2431',
  'eventLabel': 'fnsz',
  'probability': '1.0000',
  'startTime': '62.9323'},
 {'currentT': 't002',
  'endTime': '405.0000',
  'eventLabel': 'bckg',
  'probability': '1.0000',
  'startTime': '153.2431'}]

In [89]:
#print(fileNames[0:30])
testDb.patients.delete_many({})
testDb.sessions.delete_many({})
testDb.reports.delete_many({})

for files in fileNames:
    addFile(files)
    

TSE EXCEPTION ENCOUNTERED
EXC:  'tseList'
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 62.9323 bckg 1.0000', '62.9323 153.2431 fnsz 1.0000', '153.2431 405.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '62.9323', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['62.9323', '153.2431', 'fnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['153.2431', '405.0000', 'bckg', '1.0000']
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 434.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '434.0000', 'bckg', '1.0000']
[[{'currentT': 't002', 'startTime': '0.0000', 'endTime': '62.9323', 'eventLabel': 'b

TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '464.0000', 'bckg', '1.0000']
[[{'currentT': 't004', 'startTime': '0.0000', 'endTime': '120.5732', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't004', 'startTime': '120.5732', 'endTime': '129.0287', 'eventLabel': 'fnsz', 'probability': '1.0000'}, {'currentT': 't004', 'startTime': '129.0287', 'endTime': '364.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't005', 'startTime': '0.0000', 'endTime': '87.7643', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't005', 'startTime': '87.7643', 'endTime': '109.5717', 'eventLabel': 'fnsz', 'probability': '1.0000'}, {'currentT': 't005', 'startTime': '109.5717', 'endTime': '325.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't005', 'startTime': '0.0000', 'endTime': '87.7643', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't005', 'startTime': '87.7643', 'endTi

LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '184.9431', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['184.9431', '214.9989', 'fnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['214.9989', '635.0000', 'bckg', '1.0000']
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 294.0000 bckg 1.0000', '294.0000 313.0635 fnsz 1.0000', '313.0635 685.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '294.0000', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['294.0000', '313.0635', 'fnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['313.0635', '685.0000', 'bckg', '1.0000']
[[{'currentT': 't001', 'startTime': '0.0000', 'endTime': '184.9431', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't001', 'startTime': '184.9431', 'endTime': '214.9989', 'eventLabel': '

Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 43.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '43.0000', 'bckg', '1.0000']
[[{'currentT': 't001', 'startTime': '0.0000', 'endTime': '40.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't000', 'startTime': '0.0000', 'endTime': '43.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}]]
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 72.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '72.0000', 'bckg', '1.0000']
[[{'currentT': 't001', 'startTime': '0.0000', 'endTime': '40.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}]

LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '601.0000', 'bckg', '1.0000']
[[{'currentT': 't003', 'startTime': '0.0000', 'endTime': '592.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't002', 'startTime': '0.0000', 'endTime': '601.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't000', 'startTime': '0.0000', 'endTime': '300.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't001', 'startTime': '0.0000', 'endTime': '601.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't005', 'startTime': '0.0000', 'endTime': '601.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}]]
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 300.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '300.0000', 'bckg', '1.

...

TSE DATA ENTRY (parse function) :  ['664.9396', '713.9396', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['713.9396', '786.9396', 'gnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['786.9396', '885.9195', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['885.9195', '957.9195', 'gnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['957.9195', '1026.8604', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['1026.8604', '1082.6604', 'gnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['1082.6604', '1180.0000', 'bckg', '1.0000']
[[{'currentT': 't000', 'startTime': '0.0000', 'endTime': '1.0805', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't000', 'startTime': '1.0805', 'endTime': '31.8805', 'eventLabel': 'gnsz', 'probability': '1.0000'}, {'currentT': 't000', 'startTime': '31.8805', 'endTime': '96.4604', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't000', 'startTime': '96.4604', 'endTime': '177.8604', 'eventLabel': 'gnsz', 'probability': 

TSE DATA ENTRY (parse function) :  ['0.0000', '1241.0000', 'bckg', '1.0000']
TSE EXCEPTION ENCOUNTERED
EXC:  'tseList'
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 198.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '198.0000', 'bckg', '1.0000']
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 52.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '52.0000', 'bckg', '1.0000']
[[{'currentT': 't002', 'startTime': '0.0000', 'endTime': '198.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't001', 'startTime': '0.0000', 'endTime': '52.0000', 'eventLabel': 'bckg', 'probability': '1.00

TSE DATA ENTRY (parse function) :  ['449.4597', '601.0000', 'bckg', '1.0000']
[[{'currentT': 't000', 'startTime': '0.0000', 'endTime': '86.3597', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't000', 'startTime': '86.3597', 'endTime': '120.8597', 'eventLabel': 'fnsz', 'probability': '1.0000'}, {'currentT': 't000', 'startTime': '120.8597', 'endTime': '260.2201', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't000', 'startTime': '260.2201', 'endTime': '297.4201', 'eventLabel': 'fnsz', 'probability': '1.0000'}, {'currentT': 't000', 'startTime': '297.4201', 'endTime': '300.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't001', 'startTime': '0.0000', 'endTime': '300.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't003', 'startTime': '0.0000', 'endTime': '55.4530', 'eventLabel': 'bckg', 'probability': '1.0000'}, {'currentT': 't003', 'startTime': '55.4530', 'endTime': '86.6530', 'eventLabel': 'fnsz', 'probability': '1

TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '169.5470', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['169.5470', '188.8470', 'fnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['188.8470', '194.3537', 'bckg', '1.0000']
TSE DATA ENTRY (parse function) :  ['194.3537', '220.9537', 'gnsz', '1.0000']
TSE DATA ENTRY (parse function) :  ['220.9537', '300.0000', 'bckg', '1.0000']
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 209.5530 bckg 1.0000', '209.5530 255.4530 fnsz 1.0000', '255.4530 272.7799 bckg 1.0000', '272.7799 330.6799 fnsz 1.0000', '330.6799 426.8597 bckg 1.0000', '426.8597 508.1597 fnsz 1.0000', '508.1597 601.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  [

TSE EXCEPTION ENCOUNTERED
EXC:  'tseList'
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 300.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '300.0000', 'bckg', '1.0000']
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 879.0000 bckg 1.0000']
TSE DATA ENTRY (parse function) :  ['version', '=', 'tse_v1.0.0']
LEN NOT 4:  ['version', '=', 'tse_v1.0.0']
TSE DATA ENTRY (parse function) :  ['']
LEN NOT 4:  ['']
TSE DATA ENTRY (parse function) :  ['0.0000', '879.0000', 'bckg', '1.0000']
[[{'currentT': 't013', 'startTime': '0.0000', 'endTime': '300.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}], [{'currentT': 't006', 'startTime': '0.0000', 'endTime': '879.0000', 'eventLabel': 'bckg', 'probability': '1.0000'}]]
Entry (Parse Fuction: ):  ['version = tse_v1.0.0', '', '0.0000 601.

In [90]:
#print(sessionFound.count())
#print(sessionFound)
allSessions = sessions.find({})
print(allSessions.count())
#populate words
wordList = []

report1 = sessions.find_one({})['reportText']
for x in report1:
    #print(x)
    for y in (x.split(' ')):
        wordList.append(y)

newList = []
finalList =[]
x = 1 
for session in allSessions:  
    for line in session['reportText']:
        for word in line.split(' '):
            newList.append(word)
    newList = list(set(newList)&set(wordList))
    
print(newList)        


            

    

239
['are', 'discharges', 'This', 'occipital', '\n', 'brief', 'transitioning', 'right', 'prominent', 'record,', 'By', 'was', 'The', 'recording', 'not', 'Seizure', 'to:\n', 'posterior', 'a.m.,', 'INTRODUCTION:', '69', 'Abnormal', '6:37', 'following', 'region.\n', 'IMPRESSION:', 'status', 'seizures', 'at', 'maximum', 'later', 'old', 'activity.', 'epilepticus.\n', '11:18', 'patient', 'using', 'with', 'one', '1', 'Keppra,', 'minute.', 'a', 'somnolent.\n', 'by', 'DESCRIPTION', 'duration', 'Prominent', 'standard', 'digital', 'integrity', 'a.m.\n', 'of', 'lost,', 'bedside', 'sharp', 'no', 'RECORD:', 'demonstrated', 'regions,', 'on', 'hemisphere,', 'fast', 'temporal', 'EEG', 'and', 'MEDICATIONS:', 'discontinuous.', 'background', 'treated', 'Dilantin\n', 'monitor', 'region.', 'irritative', 'characterized', 'due', 'long', 'is', 'video', '3.', 'performed', 'bursts', '10-20', 'observed.\n', 'has', '1.', 'clinical', 'epileptiform', 'initial', 'refractory', 'to', 'At', 'the', 'changes', 'EKG.', 'jus

In [31]:
patientDbPrint = patients.find({})
sessionsDb = sessions.find({})
sessionList = []
for session in sessionsDb:
    if len(session.keys())>4:
        sessionList.append(session)
    #print(session)
    
reportText1 = sessionList[0]['ReportText']

reportTextString = " ".join(reportText1)

#print(reportTextString)

reportTextStringList = reportTextString.split(" ")

fDist = nltk.FreqDist(reportTextStringList)
print(fDist.items())
#print(reportTextStringList)

'''for x in reportText1:
    print("\t"+x)
    print("\n")
    

for patient in patientDbPrint:
    print(patient)
'''

KeyError: 'ReportText'

In [29]:
#fDist.most_common(30)
mostCommon = fDist.most_common(20)
xAxisVals = []
yAxisVals = []

plt.figure(figsize=(10,10))
for x in mostCommon:
    xAxisVals.append(x[0])
    yAxisVals.append(x[1])
plt.bar(xAxisVals,yAxisVals)
plt.show()

NameError: name 'fDist' is not defined

In [ ]:
'''with open(str(files),'r') as tseFile:
                    tseData = tseFile.readlines()  
                #tseData = tseData.split(' ')
                #print(files)
                #print('Something is wrong here, some of this isnt printing','\n')
                print('TSE DATA: ',tseData,'\n')
                print('Len: ',len(tseData),'\n')
                 for entry in tseData:
                        print('Entry Iteration: ',entry)
                        entryList = entry.split(' ')
                        #print("EntryList: ",entryList,"\n")
                        if len(entry)<4:
                            pass
                        else:
                            print("Found an entry",'\n')
                            print('currentEntry: ' ,entry)
                            currentT = currentFileSplit[2].split(".")
                            currentT = currentT[0]
                            tseEntry = {'segment':currentT,'startTime':entryList[0],'endTime':entryList[1],
                               'eventLabel':entryList[2],'probability':entryList[3]}
                            print("TSE ENTRY: ",tseEntry)
                            updateTseData.append(tseEntry)
                #print('TSE TYPE',type(tseData),'\n')
            
                try:
                    for entry in tseData:
                        print('Entry Iteration: ',entry)
                        entryList = entry.split(' ')
                        #print("EntryList: ",entryList,"\n")
                        if len(entry)<4:
                            pass
                        else:
                            print("Found an entry",'\n')
                            print('currentEntry: ' ,entry)
                            currentT = currentFileSplit[2].split(".")
                            currentT = currentT[0]
                            tseEntry = {'segment':currentT,'startTime':entryList[0],'endTime':entryList[1],
                               'eventLabel':entryList[2],'probability':entryList[3]}
                            print("TSE ENTRY: ",tseEntry)
                            updateTseData.append(tseEntry)
                    #tseEntry = {'startTime':tseData[0],'endTime':tseData[1],
                    #           'eventLabel':tseData[2],'probability':tseData[3]}
                except: 
                    print("Found and ERRRORRORORORO")
                    tseEntry='Error''''

In [33]:
class channel(object):
    def __init__(self,edfFile,label=None,transducer=None,dimensions=None,
                physMin=None,physMax=None,digMin=None,digMax=None,
                 preFilter=None,sampleRate=None,notes=None,channelIndex=None,byteLength=None):
        self.edfFile = edfFile
        self.label = str(label)
        self.sampleRate = int(sampleRate)
        self.transducer = str(transducer)
        self.dimensions = dimensions
        self.physMin = physMin
        self.physMax = physMax
        self.digMin = digMin
        self.digMax = digMax
        self.preFilter = preFilter
        self.notes  = notes
        self.channelIndex = int(channelIndex)
        self.byteLength = byteLength
        #self.indexStart = indexStart
    
    def __str__(self):
        if self.label==None:
            return "None"
        else:
            returnString = ("Label: "+str(self.label) + "\nSample Rate"+str(self.sampleRate)+
            "\nTransducer: "+str(self.transducer)+"\nDimensions: "+str(self.dimensions)+
            "\nphysMin: "+str(self.physMin)+"\nphysMax: "+str(self.physMax)+
            "\ndigMin: "+str(self.digMin) +"\ndigMax: "+str(self.digMax)+ "\npreFilter: "+str(self.preFilter)+
            "\nNotes: "+str(self.notes) + "\nChannelIndex: "+str(self.channelIndex) + "\nbyteLength: "+str(self.byteLength))
        return returnString
    
    def channelData(self,start,duration,channelNumber = 0,sensitivity = 1):
        '''
        Returns data points for desired area
        start: seconds from start of record
        duration: time  of record desired in seconds
        ##########This might be easier to do within original edf class
        '''
        toReturn = []
        startByte = start * self.sampleRate * 2
        seekLocation = int(self.channelIndex + startByte)  #need to fix this
        numberOfBytes = int(self.sampleRate) * duration # * 2
        self.edfFile.edfRawData.seek(seekLocation)
        for i in range(numberOfBytes):
            value = struct.unpack('h',self.edfFile.edfRawData.read(2))[0]
            value = np.array(value)*sensitivity
            value -= channelNumber*20*sensitivity
            toReturn.append(value)
            #toReturn.append(struct.unpack('h',self.edfFile.edfRawData.read(2))) 
        return toReturn

    def allChannelData(self):
        toReturn = []
        self.edfFile.edfRawData.seek(self.channelIndex)
        for i in range(int(self.byteLength/2)):
            toReturn.append(struct.unpack('h',self.edfFile.edfRawData.read(2)))
        return toReturn
        
    def getLabel(self):
        return str(self.label)
    
    def getSampleRate(self):
        return self.sampleRate
    
    def getChannelIndex(self):
        return self.channelIndex
    
    def getTransducer(self):
        return self.transducer

    def getDimensions(self):
        return self.dimensions
    
    def getPhysMin(self):
        return self.physMin
    
    def getPhysMax(self):
        return self.physMax
    
    def getDigMin(self):
        return self.digMin
    
    def getDigMax(self):
        return self.digMax
    
    def getPreFilter(self):
        return self.preFilter
    
    def getNotes(self):
        return self.notes
    
    def getByteLength(self):
        return self.byteLength

In [34]:
class edfData(object):
    def __init__(self,fileId):
        self.fileId=fileId
        
    def __str__(self):
        return ("version: " + str(self.version) + "\nPatient Id: "+str(self.patientId) 
                + "\nrecordId" + str(self.recordId) + "\nStart Date: " + str(self.startTime)
                + "\nStart Time: " + str(self.startTime)
                + "\nheader Bytes: " + str(self.headerBytes) +"\nReserve Bytes: " +str(self.reservedBytes)
                + "\nNum Records :" + str(self.nRecords) + "\nNum Signals :" + str(self.nSignals) 
                + "\nDuration: "+ str(self.duration) + "\nFile Size: "+str(self.fileSize))
                
                
    def loadFile(self,filepath):
        self.filePath = filepath
        self.fileSize = os.path.getsize(filepath)
        self.edfRawData = open(filepath,'rb')
        
    def readBitsTest(self):
        self.edfRawData.seek(0)
        bits = self.edfRawData.read(10000)
        self.edfRawData.seek(0)
        print(self.edfRawData.read(10))
        print("Some Bits: "+str(bits))
        return bits
    
    def readSignalHeaderBits(self,bitsIn,nSignals,nBits):
            returnArray = []
            for x in range(nSignals):
                returnArray.append(bitsIn.read(nBits))
            return returnArray
    
    def parseEdf(self):
        '''
            This function parses the edf file getting the values of 
            the header fields. It also creates a channel object with 
            information about each channel, including the eeg tracing data from each channel.
        '''
        #Header Fields
        self.version = str(self.edfRawData.read(8))
        self.patientId = str(self.edfRawData.read(80))
        self.recordId = str(self.edfRawData.read(80))
        self.startDate = str(self.edfRawData.read(8))
        self.startTime = str(self.edfRawData.read(8))
        self.headerBytes = int(self.edfRawData.read(8))
        self.reservedBytes = str(self.edfRawData.read(44))
        self.nRecords = int(self.edfRawData.read(8))
        self.duration = float(self.edfRawData.read(8))
        self.nSignals = int(self.edfRawData.read(4))
        
        #Create channel object for each channel
        self.channels = {}
        channelFields = ['labels','transducer','dimensions','physMin','physMax','digMin','digMax',
                        'preFilter','sampleRate','reservedNotes']
        self.channels['labels'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,16)
        self.channels['transducer'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,80)
        self.channels['dimensions'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,8)
        self.channels['physMin'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,8)
        self.channels['physMax'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,8)
        self.channels['digMin'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,8)
        self.channels['digMax'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,8)
        self.channels['preFilter'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,80)
        self.channels['sampleRate'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,8)
        self.channels['reservedNotes'] = self.readSignalHeaderBits(self.edfRawData,self.nSignals,32)
        
        self.channelObjects = []
        self.sampleRate = self.channels['sampleRate'][0]
        channelDataStart = self.headerBytes
        
        #This loop creates and add channel objects to self.channelObjects
        for i in range(int(self.nSignals)):
            
            channelValues ={'filepath':self.filePath}
            byteLength = int(self.channels['sampleRate'][i])*self.nRecords*2
            channelIndex = channelDataStart
            channelDataStart +=byteLength
            
            for j in channelFields:
                try:
                    channelValues[j]=(self.channels[j][i])
                except:
                    channelValues[j] = None
            self.channelObjects.append(
                channel(self,channelValues['labels'],channelValues['transducer'],
                        channelValues['dimensions'],channelValues['physMin'],channelValues['physMax'],
                        channelValues['digMin'],channelValues['digMax'],channelValues['preFilter'],
                        channelValues['sampleRate'],channelValues['reservedNotes'],
                        channelIndex,byteLength))
            
    def data(self,start,duration):
        sampleData = []
        j = 0
        for x in self.channelObjects:
            sampleData.append([x.getLabel(),x.channelData(start,duration)])
            j+=1
        return sampleData
    
    def dataDictionary(self,start,duration):
        sampleData = []
        j = 0
        for x in self.channelObjects:
            sampleData.append({x.getLabel():x.channelData(start,duration)})
            j+=1
        return sampleData
    
    def dataForGraph(self,start,duration,sensitivity=1):
        sampleData = []
        j=0
        for x in self.channelObjects:
            sampleData.append([x.getLabel(),x.channelData(start,duration,j,sensitivity)])
            j+=1
        return sampleData
    
    def allData(self):
        '''
        Return[sampleRate,{channelData}]
        '''
        channelData = {}
        for x in self.channelObjects:
            channelData[str(x.getLabel())]=np.array(x.allChannelData())
        return[int(self.sampleRate),channelData]
            
            
    
    def patientId(self):
        return self.patientId
    
    def recordId(self):
        return self.recordId
    
    def startDate(self):
        return self.startDate
    
    def startTime(self):
        return self.startTime
    
    def headerBytes(self):
        return self.headerBytes
    
    def reservedBytes(self):
        return self.reservedBytes
    
    def duration(self):
        return self.duration
    
    def nRecords(self):
        return self.nRecords
    
    def numSignals(self):
        return self.nSignals
    
    def sampleRate(self):
        return self.sampleRate

    def channelLabels(self):
        labels = []
        for channel in self.channelObjects:
            labels.append(channel.label())
        return labels
    
    def totalSamples(self):
        duration = int(self.sampleRate) * int(self.nRecords)
        return duration
    
    def testChannelPrint(self):
        print(self.channelObjects[2])